### Base de Dados

**Input**: 
* input/factors/YYYYMMDD.csv - fatores de todas ações listadas na NYSE na frequência de um minuto do dia DD-MM-YYYY.
* input/returns/YYYYMMDD.csv - retornos de todas ações listadas na NYSE na frequência de um minuto do dia DD-MM-YYYY.

**Output**: 
* output/data/median_breakpoint/equal_weighted/YYYYMMDD.csv - retornos de todas ações listadas na NYSE e portfólios baseado em fatores a partir desses ativos na frequência de um minuto do dia DD-MM-YYYY.

O objetivo desse notebook é juntar duas bases de dados, uma contendo dados de retornos das ações e outro contendo os decis de cada ação. A partir desse merge, vamos criar portfólios Value Weighted dos fatores utilizando os tercis como Breakpoints.

In [2]:
# pacotes
import numpy as np
import pandas as pd

In [3]:
# oculta mensagens de avisos
import warnings
warnings.filterwarnings("ignore")

In [3]:
# pd.set_option('display.max_columns', None)

In [7]:
pd.set_option('display.max_rows', None)

In [1]:
day = '20050103'

In [4]:
factors_path = f'../../../input/factors/{day}.csv'
factors = pd.read_csv(factors_path, index_col=0)
# precisamos dropar todas ações que não tem TAQ_TICKER, pois é a única variável q conseguimos ligar na outra base
factors = factors[factors['TAQ_TICKER'] != '<undefined>']

In [8]:
factors

date                            COMNAM TAQ_TICKER     MARKETCAP  \
10001  20050103                   ENERGY WEST INC       EWST  1.733533e+04   
10002  20050103     BANCTRUST FINANCIAL GROUP INC       BTFG  2.626304e+05   
10012  20050103         D P A C TECHNOLOGIES CORP       DPAC  2.064684e+04   
10025  20050103              A E P INDUSTRIES INC       AEPI  1.245621e+05   
10026  20050103            J & J SNACK FOODS CORP       JJSF  4.289059e+05   
10028  20050103             D G S E COMPANIES INC       DGSE  1.493552e+04   
10032  20050103                       PLEXUS CORP       PLXS  5.179560e+05   
10042  20050103             CANYON RESOURCES CORP        CAU  3.493920e+04   
10044  20050103  ROCKY MOUNTAIN CHOCOLATE FAC INC       RMCF  6.252400e+04   
10051  20050103       HANGER ORTHOPEDIC GROUP INC        HGR  1.743583e+05   
10056  20050103                NEWMIL BANCORP INC       NMIL  1.334184e+05   
10078  20050103              SUN MICROSYSTEMS INC       SUNW  1.726087e+07   
10085  20050103                           U I C I        UCI  1.500336e+06   
10089  20050103      ALPHA TECHNOLOGIES GROUP INC       ATGI  5.972400e+03   
10092  20050103          4 KIDS ENTERTAINMENT INC        KDE  2.696375e+05   
10100  20050103    AMERICAN CLAIMS EVALUATION INC       AMCE  1.151820e+04   
10104  20050103                       ORACLE CORP       ORCL  7.006545e+07   
10107  20050103                    MICROSOFT CORP       MSFT  2.909371e+08   
10108  20050103          SUNGARD DATA SYSTEMS INC        SDS  8.102832e+06   
10119  20050103      21ST CENTURY INSURANCE GROUP         TW  1.165092e+06   
10137  20050103              ALLEGHENY ENERGY INC        AYE  2.657315e+06   
10138  20050103            T ROWE PRICE GROUP INC       TROW  7.991629e+06   
10143  20050103         O S I PHARMACEUTICALS INC       OSIP  3.684046e+06   
10145  20050103       HONEYWELL INTERNATIONAL INC        HON  3.036393e+07   
10147  20050103                     E M C CORP MA        EMC  3.529719e+07   
10163  20050103                        X RITE INC       XRIT  3.239334e+05   
10180  20050103                         AKORN INC        AKN  8.070270e+04   
10182  20050103                    TECH DATA CORP       TECD  2.606857e+06   
10200  20050103                     REPLIGEN CORP       RGEN  8.721460e+04   
10205  20050103                        L S B CORP       LSBX  8.131875e+04   
10211  20050103                      WESTCORP INC        WES  2.365409e+06   
10225  20050103                FORTUNE BRANDS INC         FO  1.101329e+07   
10232  20050103        ELMIRA SAVINGS BANK FSB NY       ESBK  3.342800e+04   
10238  20050103             BAY VIEW CAPITAL CORP        BVC  1.037266e+05   
10239  20050103               BALDWIN & LYONS INC      BWINB  3.241858e+05   
10252  20050103          INDEPENDENT BANK CORP MA       INDB  5.066776e+05   
10253  20050103     DOCUMENT SECURITY SYSTEMS INC        DMC  7.703535e+04   
10257  20050103                     TEAMSTAFF INC       TSTF  3.295292e+04   
10258  20050103      AVANT IMMUNOTHERAPEUTICS INC       AVAN  1.519685e+05   
10259  20050103                 SIGMA DESIGNS INC       SIGM  2.075451e+05   
10271  20050103                     MASSBANK CORP       MASB  1.621340e+05   
10272  20050103                           TEKELEC       TKLC  1.318090e+06   
10290  20050103            HARLEYSVILLE GROUP INC       HGIC  7.119090e+05   
10297  20050103  NEW HAMPSHIRE THRIFT BNCSHRS INC       NHTB  6.895956e+04   
10299  20050103            LINEAR TECHNOLOGY CORP       LLTC  1.174821e+07   
10302  20050103        CYPRESS SEMICONDUCTOR CORP         CY  1.434819e+06   
10304  20050103              AMCORE FINANCIAL INC       AMFI  7.898042e+05   
10308  20050103              TOMPKINS TRUSTCO INC        TMP  4.249773e+05   
10318  20050103                      BALCHEM CORP        BCP  1.734145e+05   
10324  20050103                      GENZYME CORP       GENZ  1.429728e+07   
10342  20050103                  

In [5]:
# returns dataframe
returns_path = f'../../../input/returns/{day}.csv'
returns = pd.read_csv(returns_path, index_col=0)

### Functions

Como a metodologia para se criar o portfólio é a mesma, isso é, comprado em todos ativos acima da mediana e vendido em todos ativos abaixo da mediana, vamos criar funções que façam isso recebendo a coluna do fator em questão como parâmetro.

In [5]:
def portfolio_position(col):
    long_position = []      # posição comprado
    short_position = []     # posição vendido  

    # primeiro, precisamos dropar as linhas tais que tem valor NaN no parâmetro de localidade do fator
    temp = factors[factors[col].notna()]
    """
    Criamos um loop com o critério:
    acima da mediana '5' (estritamente), então o portfolio assume a posição comprado
    abaixo da mediana '5' (fracamente), então o portfolio assume a posição vendido
    """
    for permno in temp.index:
        if temp.loc[permno][col] > 5:
            long_position.append(temp.loc[permno]['TAQ_TICKER'])
        else:
            short_position.append(temp.loc[permno]['TAQ_TICKER'])
    """
    agora precisamos criar dois loops, um para cada lista:
    o loop deve verificar se o ticker dentro da lista é uma das colunas da base de retornos,
    isso é, verifica se temos dados de retornos para essa ação.
    """

    drop_long_position = []
    drop_short_position = []

    for ticker in long_position:
        if ticker not in returns.columns:
            drop_long_position.append(ticker)

    for ticker in drop_long_position:
        long_position.remove(ticker)

    for ticker in short_position:   
        if ticker not in returns.columns:
            drop_short_position.append(ticker)

    for ticker in drop_short_position:
        short_position.remove(ticker)

    return(long_position, short_position)

In [6]:
def portfolio_formation(col):
    # usaremos a função portfolio_position() para obtermos as firmas na posição comprada e vendida
    long_position, short_position = portfolio_position(col)
    # a nova coluna do fator se chamará:
    new_col = col[6].upper() + col[7:] + ' Factor'
    """
    O portfolio é formado subtraindo os retornos médio (equal weighted) das ações em short_position
    dos retornos médio (equal weighted) das ações em long_position
    """
    returns[new_col] = returns[long_position].mean(axis=1) - returns[short_position].mean(axis=1)

### Data Generator Loop

Esse loop deverá gerar dados diários (um .csv para cada dia) com todos retornos e todos portfolios (para cada fator).

In [7]:
# precisamos criar um range de datas para o período de dados que temos
bdates = pd.bdate_range('2005-01-01', '2019-12-31')
bdates_ = []

# precisamos torná-los da maneira que os csv's estão nomeados
for date in bdates:
    day = str(date)[:4] + str(date)[5:7] + str(date)[8:10]
    bdates_.append(day)

In [8]:
for day in bdates_:
    try:
        # factors dataframe
        factors_path = f'../../../input/factors/{day}.csv'
        factors = pd.read_csv(factors_path, index_col=0)
        # precisamos dropar todas ações que não tem TAQ_TICKER, pois é a única variável q conseguimos ligar na outra base
        factors = factors[factors['TAQ_TICKER'] != '<undefined>']
        
        # returns dataframe
        returns_path = f'../../../input/returns/{day}.csv'
        returns = pd.read_csv(returns_path, index_col=0)

        # agora precisamos fazer o loop que para cada coluna de pNYSE_factors, forma-se um portfolio
        pNYSE_factors = factors.columns[4:]
        for pNYSE in pNYSE_factors:
            portfolio_formation(pNYSE)

        # precisamos agora fazer a conversão do dataframe para csv
        output_path = f'../../../output/data/median_breakpoint/equal_weighted/{day}.csv'
        returns.to_csv(output_path, sep=',', encoding='utf-8')
    except:
        pass